In [1]:
import random
import csv
import time

def generate_mobile_numbers(count):
    """Generates a list of random 10-digit mobile numbers."""
    mobile_numbers = []
    for _ in range(count):
        # Generate a random 10-digit number, ensuring the first digit is not zero
        number = f"{random.randint(6, 9)}{random.randint(100000000, 999999999)}"
        mobile_numbers.append(number)
    return mobile_numbers

def save_to_csv(filename, data):
    """Saves a list of mobile numbers to a CSV file."""
    with open(filename, mode='w', newline='') as file:
        writer = csv.writer(file)
        writer.writerow(["Mobile Number"])  # Adding header
        for number in data:
            writer.writerow([number])

# Number of mobile numbers to generate
total_numbers = 15000

# Start time measurement
start_time = time.time()

# Generate mobile numbers
mobile_numbers = generate_mobile_numbers(total_numbers)

# Save the generated numbers to a CSV file
csv_filename = "mobile_numbers.csv"
save_to_csv(csv_filename, mobile_numbers)

# End time measurement
end_time = time.time()

execution_time = end_time - start_time
print(f"{total_numbers} mobile numbers saved to '{csv_filename}'.")
print(f"Execution Time: {execution_time:.2f} seconds.")


15000 mobile numbers saved to 'mobile_numbers.csv'.
Execution Time: 0.03 seconds.


In [3]:
import csv
import time
from collections import defaultdict

class TrieNode:
    """Node structure for the hierarchical data storage."""
    def __init__(self):
        self.children = defaultdict(TrieNode)  # Child nodes
        self.numbers = []  # Store numbers ending at this node

class MobileNumberTrie:
    """Trie structure to store mobile numbers in a hierarchical manner."""
    def __init__(self):
        self.root = TrieNode()

    def insert(self, number):
        """Insert a number into the trie."""
        current = self.root
        for digit in number:
            current = current.children[digit]
        current.numbers.append(number)

    def display(self, node=None, prefix=""):
        """Recursively display the structure."""
        if node is None:
            node = self.root
        for digit, child in node.children.items():
            print(f"{prefix}{digit}")
            self.display(child, prefix + digit)

def read_mobile_numbers_from_csv(filename):
    """Reads mobile numbers from a CSV file."""
    mobile_numbers = []
    with open(filename, 'r') as file:
        reader = csv.reader(file)
        next(reader)  # Skip the header
        for row in reader:
            mobile_numbers.append(row[0])  # Assuming numbers are in the first column
    return mobile_numbers

# Start measuring time
start_time = time.time()

# Load mobile numbers from the CSV file
csv_filename = "mobile_numbers.csv"
mobile_numbers = read_mobile_numbers_from_csv(csv_filename)

# Create a Trie and insert all mobile numbers
trie = MobileNumberTrie()
for number in mobile_numbers:
    trie.insert(number)

# End measuring time
end_time = time.time()

# Display the hierarchical structure
print("Displaying the hierarchical structure of mobile numbers:")
trie.display()

# Calculate and print execution time
execution_time = end_time - start_time
print(f"\nExecution Time: {execution_time:.2f} seconds")


Displaying the hierarchical structure of mobile numbers:
8
82
825
8255
82554
825540
8255406
82554067
825540671
8255406710
82550
825502
8255026
82550269
825502698
8255026982
82555
825554
8255544
82555449
825554490
8255544901
825551
8255519
82555190
825551900
8255519008
8257
82575
825754
8257548
82575485
825754859
8257548598
82573
825730
8257305
82573054
825730543
8257305436
8257308
82573080
825730803
8257308037
8251
82517
825170
8251708
82517089
825170899
8251708999
82510
825100
8251008
82510081
825100813
8251008135
8251001
82510015
825100152
8251001520
825108
8251089
82510897
825108970
8251089703
82518
825189
8251890
82518907
825189078
8251890782
82515
825153
8251534
82515349
825153492
8251534920
82511
825112
8251125
82511253
825112538
8251125381
8250
82506
825068
8250682
82506821
825068218
8250682180
82503
825032
8250324
82503245
825032457
8250324570
82508
825084
8250845
82508455
825084555
8250845556
82507
825073
8250731
82507318
825073189
8250731891
8252
82523
825236
8252361
82523618

In [4]:
pip install tenseal

Note: you may need to restart the kernel to use updated packages.


In [7]:
import tenseal as ts
import time
from collections import defaultdict
import csv
import random


class TrieNode:
    """Node structure for hierarchical data storage."""
    def __init__(self):
        self.children = defaultdict(TrieNode)
        self.lane_locations = {}  # Maps digit to (lane, location)


class MobileNumberTrie:
    """Trie structure to store mobile numbers hierarchically."""
    def __init__(self):
        self.root = TrieNode()
        self.lane_counter = 1
        self.location_counter = 1

    def insert(self, number):
        """Insert a number into the trie and assign lane and location."""
        current = self.root
        for digit in number:
            if digit not in current.lane_locations:
                current.lane_locations[digit] = (self.lane_counter, self.location_counter)
                self.location_counter += 1
            current = current.children[digit]
        self.lane_counter += 1
        self.location_counter = 1  # Reset location counter for each lane

    def search_lane(self, prefix):
        """Get the lane and locations for the given prefix."""
        current = self.root
        for digit in prefix:
            if digit in current.children:
                current = current.children[digit]
            else:
                return None  # Prefix not found
        return current.lane_locations


def read_mobile_numbers_from_csv(filename):
    """Reads mobile numbers from a CSV file."""
    mobile_numbers = []
    with open(filename, 'r') as file:
        reader = csv.reader(file)
        next(reader)  # Skip header
        for row in reader:
            mobile_numbers.append(row[0])  # Assuming the first column has the numbers
    return mobile_numbers


def private_digit_match(server_lanes, encrypted_digit, r, context):
    """Perform homomorphic computation for digit matching."""
    results = []
    for digit, (lane, location) in server_lanes.items():
        enc_digit = ts.bfv_vector(context, [int(digit)])  # Encrypt server digit
        result = (encrypted_digit - enc_digit) * r
        results.append((result, lane, location))
    return results


# Client-Side Encryption Setup
context = ts.context(ts.SCHEME_TYPE.BFV, poly_modulus_degree=8192, plain_modulus=1032193)
context.generate_galois_keys()

# Start the timer
start_time = time.time()

# Step 1: Read and Build the Trie
csv_filename = "mobile_numbers.csv"
mobile_numbers = read_mobile_numbers_from_csv(csv_filename)

trie = MobileNumberTrie()
for number in mobile_numbers:
    trie.insert(number)

# Step 2: Simulate Private Search
client_number = "".join(random.choices("0123456789", k=10))  # Generate random 10-digit number
r = random.randint(1, 100)  # Random value for privacy

print(f"Client is searching for the number: {client_number}")

prefix = ""
found = True
for index, digit in enumerate(client_number):
    # Encrypt the current digit
    encrypted_digit = ts.bfv_vector(context, [int(digit)])

    # Server checks the lane corresponding to the current prefix
    server_lanes = trie.search_lane(prefix)
    if not server_lanes:
        print(f"Number {client_number} not found.")
        found = False
        break

    # Perform homomorphic digit match
    results = private_digit_match(server_lanes, encrypted_digit, r, context)

    # Client decrypts the results
    decrypted_results = [(res.decrypt()[0], lane, loc) for res, lane, loc in results]

    # Check if any result is 0 (indicating a match)
    matched = False
    for decrypted_value, lane, loc in decrypted_results:
        if decrypted_value == 0:
            matched = True
            prefix += digit
            print(f"Match found for digit {digit} at lane {lane}, location {loc}.")
            break

    if not matched:
        print(f"Number {client_number} not found at digit {index + 1}.")
        found = False
        break

if found:
    print(f"Number {client_number} is present in the server.")

# End the timer
end_time = time.time()
execution_time = end_time - start_time

print(f"\nExecution Time: {execution_time:.2f} seconds")


Client is searching for the number: 7850046103
Match found for digit 7 at lane 9, location 1.
Match found for digit 8 at lane 9, location 2.
Match found for digit 5 at lane 86, location 1.
Match found for digit 0 at lane 295, location 1.
Number 7850046103 not found at digit 5.

Execution Time: 1.00 seconds


In [11]:
import tenseal as ts
import time
from collections import defaultdict
import csv
import random


class TrieNode:
    """Node structure for hierarchical data storage."""
    def __init__(self):
        self.children = defaultdict(TrieNode)
        self.lane_locations = {}  # Maps digit to (lane, location)


class MobileNumberTrie:
    """Trie structure to store mobile numbers hierarchically."""
    def __init__(self):
        self.root = TrieNode()
        self.lane_counter = 1
        self.location_counter = 1

    def insert(self, number):
        """Insert a number into the trie and assign lane and location."""
        current = self.root
        for digit in number:
            if digit not in current.lane_locations:
                current.lane_locations[digit] = (self.lane_counter, self.location_counter)
                self.location_counter += 1
            current = current.children[digit]
        self.lane_counter += 1
        self.location_counter = 1  # Reset location counter for each lane

    def search_lane(self, prefix):
        """Get the lane and locations for the given prefix."""
        current = self.root
        for digit in prefix:
            if digit in current.children:
                current = current.children[digit]
            else:
                return None  # Prefix not found
        return current.lane_locations


def read_mobile_numbers_from_csv(filename):
    """Reads mobile numbers from a CSV file."""
    mobile_numbers = []
    with open(filename, 'r') as file:
        reader = csv.reader(file)
        next(reader)  # Skip header
        for row in reader:
            mobile_numbers.append(row[0])  # Assuming the first column has the numbers
    return mobile_numbers


def private_digit_match(server_lanes, encrypted_digit, r, context):
    """Perform homomorphic computation for digit matching."""
    results = []
    for digit, (lane, location) in server_lanes.items():
        enc_digit = ts.bfv_vector(context, [int(digit)])  # Encrypt server digit
        result = (encrypted_digit - enc_digit) * r
        results.append((result, lane, location))
    return results


# Client-Side Encryption Setup
context = ts.context(ts.SCHEME_TYPE.BFV, poly_modulus_degree=8192, plain_modulus=1032193)
context.generate_galois_keys()

# Start the timer
start_time = time.time()

# Step 1: Read and Build the Trie
csv_filename = "mobile_numbers.csv"
mobile_numbers = read_mobile_numbers_from_csv(csv_filename)

trie = MobileNumberTrie()
for number in mobile_numbers:
    trie.insert(number)

# Step 2: Simulate Private Search for 100 Random Numbers
# First digit should start from 6, 7, 8, or 9
random_numbers = []
for _ in range(10):
    first_digit = random.choice(['6', '7', '8', '9'])
    remaining_digits = "".join(random.choices("0123456789", k=9))  # Generate next 9 digits
    random_number = first_digit + remaining_digits
    random_numbers.append(random_number)

print(f"Client is searching for the following 100 random numbers...\n")

# Step 3: Perform Search for Each Random Number
for client_number in random_numbers:
    prefix = ""
    found = True
    r = random.randint(1, 10)  # Random value for privacy

    print(f"\nSearching for number: {client_number}")
    for index, digit in enumerate(client_number):
        # Encrypt the current digit
        encrypted_digit = ts.bfv_vector(context, [int(digit)])

        # Server checks the lane corresponding to the current prefix
        server_lanes = trie.search_lane(prefix)
        if not server_lanes:
            print(f"Number {client_number} not found.")
            found = False
            break

        # Perform homomorphic digit match
        results = private_digit_match(server_lanes, encrypted_digit, r, context)

        # Client decrypts the results
        decrypted_results = [(res.decrypt()[0], lane, loc) for res, lane, loc in results]

        # Check if any result is 0 (indicating a match)
        matched = False
        for decrypted_value, lane, loc in decrypted_results:
            if decrypted_value == 0:
                matched = True
                prefix += digit
                print(f"Match found for digit {digit} at lane {lane}, location {loc}.")
                break

        if not matched:
            print(f"Number {client_number} not found at digit {index + 1}.")
            found = False
            break

    if found:
        print(f"Number {client_number} is present in the server.")

# End the timer
end_time = time.time()
execution_time = end_time - start_time

print(f"\nExecution Time for 10 Random Numbers: {execution_time:.2f} seconds")


Client is searching for the following 100 random numbers...


Searching for number: 9136196942
Match found for digit 9 at lane 3, location 1.
Match found for digit 1 at lane 3, location 2.
Match found for digit 3 at lane 24, location 1.
Match found for digit 6 at lane 9887, location 1.
Number 9136196942 not found at digit 5.

Searching for number: 8093924435
Match found for digit 8 at lane 1, location 1.
Number 8093924435 not found at digit 2.

Searching for number: 6939064464
Match found for digit 6 at lane 2, location 1.
Match found for digit 9 at lane 47, location 1.
Match found for digit 3 at lane 467, location 1.
Match found for digit 9 at lane 2602, location 1.
Number 6939064464 not found at digit 5.

Searching for number: 6548938711
Match found for digit 6 at lane 2, location 1.
Match found for digit 5 at lane 6, location 1.
Match found for digit 4 at lane 693, location 1.
Match found for digit 8 at lane 9537, location 1.
Number 6548938711 not found at digit 5.

Searching for nu

In [12]:
import tenseal as ts
import time
from collections import defaultdict
import csv
import random


class TrieNode:
    """Node structure for hierarchical data storage."""
    def __init__(self):
        self.children = defaultdict(TrieNode)
        self.lane_locations = {}  # Maps digit to (lane, location)


class MobileNumberTrie:
    """Trie structure to store mobile numbers hierarchically."""
    def __init__(self):
        self.root = TrieNode()
        self.lane_counter = 1
        self.location_counter = 1

    def insert(self, number):
        """Insert a number into the trie and assign lane and location."""
        current = self.root
        for digit in number:
            if digit not in current.lane_locations:
                current.lane_locations[digit] = (self.lane_counter, self.location_counter)
                self.location_counter += 1
            current = current.children[digit]
        self.lane_counter += 1
        self.location_counter = 1  # Reset location counter for each lane

    def search_lane(self, prefix):
        """Get the lane and locations for the given prefix."""
        current = self.root
        for digit in prefix:
            if digit in current.children:
                current = current.children[digit]
            else:
                return None  # Prefix not found
        return current.lane_locations


def read_mobile_numbers_from_csv(filename):
    """Reads mobile numbers from a CSV file."""
    mobile_numbers = []
    with open(filename, 'r') as file:
        reader = csv.reader(file)
        next(reader)  # Skip header
        for row in reader:
            mobile_numbers.append(row[0])  # Assuming the first column has the numbers
    return mobile_numbers


def private_digit_match(server_lanes, encrypted_digit, r, context):
    """Perform homomorphic computation for digit matching."""
    results = []
    for digit, (lane, location) in server_lanes.items():
        enc_digit = ts.bfv_vector(context, [int(digit)])  # Encrypt server digit
        result = (encrypted_digit - enc_digit) * r
        results.append((result, lane, location))
    return results


# Client-Side Encryption Setup
context = ts.context(ts.SCHEME_TYPE.BFV, poly_modulus_degree=8192, plain_modulus=1032193)
context.generate_galois_keys()

# Start the timer
start_time = time.time()

# Step 1: Read and Build the Trie
csv_filename = "mobile_numbers.csv"
mobile_numbers = read_mobile_numbers_from_csv(csv_filename)

trie = MobileNumberTrie()
for number in mobile_numbers:
    trie.insert(number)

# Step 2: Simulate Private Search for 100 Random Numbers
# First digit should start from 6, 7, 8, or 9
random_numbers = []
for _ in range(100):
    first_digit = random.choice(['6', '7', '8', '9'])
    remaining_digits = "".join(random.choices("0123456789", k=9))  # Generate next 9 digits
    random_number = first_digit + remaining_digits
    random_numbers.append(random_number)

print(f"Client is searching for the following 100 random numbers...\n")

# Step 3: Perform Search for Each Random Number
for client_number in random_numbers:
    prefix = ""
    found = True
    r = random.randint(1, 10)  # Random value for privacy

    print(f"\nSearching for number: {client_number}")
    for index, digit in enumerate(client_number):
        # Encrypt the current digit
        encrypted_digit = ts.bfv_vector(context, [int(digit)])

        # Server checks the lane corresponding to the current prefix
        server_lanes = trie.search_lane(prefix)
        if not server_lanes:
            print(f"Number {client_number} not found.")
            found = False
            break

        # Perform homomorphic digit match
        results = private_digit_match(server_lanes, encrypted_digit, r, context)

        # Client decrypts the results
        decrypted_results = [(res.decrypt()[0], lane, loc) for res, lane, loc in results]

        # Check if any result is 0 (indicating a match)
        matched = False
        for decrypted_value, lane, loc in decrypted_results:
            if decrypted_value == 0:
                matched = True
                prefix += digit
                print(f"Match found for digit {digit} at lane {lane}, location {loc}.")
                break

        if not matched:
            print(f"Number {client_number} not found at digit {index + 1}.")
            found = False
            break

    if found:
        print(f"Number {client_number} is present in the server.")

# End the timer
end_time = time.time()
execution_time = end_time - start_time

print(f"\nExecution Time for 100 Random Numbers: {execution_time:.2f} seconds")


Client is searching for the following 100 random numbers...


Searching for number: 9399062286
Match found for digit 9 at lane 3, location 1.
Match found for digit 3 at lane 52, location 1.
Match found for digit 9 at lane 349, location 1.
Match found for digit 9 at lane 5221, location 1.
Number 9399062286 not found at digit 5.

Searching for number: 6599522598
Match found for digit 6 at lane 2, location 1.
Match found for digit 5 at lane 6, location 1.
Match found for digit 9 at lane 6, location 2.
Match found for digit 9 at lane 4622, location 1.
Number 6599522598 not found at digit 5.

Searching for number: 7547547302
Match found for digit 7 at lane 9, location 1.
Match found for digit 5 at lane 65, location 1.
Match found for digit 4 at lane 510, location 1.
Match found for digit 7 at lane 2263, location 1.
Match found for digit 5 at lane 6930, location 1.
Number 7547547302 not found at digit 6.

Searching for number: 9976837334
Match found for digit 9 at lane 3, location 1.
Match f

In [13]:
import tenseal as ts
import time
from collections import defaultdict
import csv
import random


class TrieNode:
    """Node structure for hierarchical data storage."""
    def __init__(self):
        self.children = defaultdict(TrieNode)
        self.lane_locations = {}  # Maps digit to (lane, location)


class MobileNumberTrie:
    """Trie structure to store mobile numbers hierarchically."""
    def __init__(self):
        self.root = TrieNode()
        self.lane_counter = 1
        self.location_counter = 1

    def insert(self, number):
        """Insert a number into the trie and assign lane and location."""
        current = self.root
        for digit in number:
            if digit not in current.lane_locations:
                current.lane_locations[digit] = (self.lane_counter, self.location_counter)
                self.location_counter += 1
            current = current.children[digit]
        self.lane_counter += 1
        self.location_counter = 1  # Reset location counter for each lane

    def search_lane(self, prefix):
        """Get the lane and locations for the given prefix."""
        current = self.root
        for digit in prefix:
            if digit in current.children:
                current = current.children[digit]
            else:
                return None  # Prefix not found
        return current.lane_locations


def read_mobile_numbers_from_csv(filename):
    """Reads mobile numbers from a CSV file."""
    mobile_numbers = []
    with open(filename, 'r') as file:
        reader = csv.reader(file)
        next(reader)  # Skip header
        for row in reader:
            mobile_numbers.append(row[0])  # Assuming the first column has the numbers
    return mobile_numbers


def private_digit_match(server_lanes, encrypted_digit, r, context):
    """Perform homomorphic computation for digit matching."""
    results = []
    for digit, (lane, location) in server_lanes.items():
        enc_digit = ts.bfv_vector(context, [int(digit)])  # Encrypt server digit
        result = (encrypted_digit - enc_digit) * r
        results.append((result, lane, location))
    return results


# Client-Side Encryption Setup
context = ts.context(ts.SCHEME_TYPE.BFV, poly_modulus_degree=8192, plain_modulus=1032193)
context.generate_galois_keys()

# Start the timer
start_time = time.time()

# Step 1: Read and Build the Trie
csv_filename = "mobile_numbers.csv"
mobile_numbers = read_mobile_numbers_from_csv(csv_filename)

trie = MobileNumberTrie()
for number in mobile_numbers:
    trie.insert(number)

# Step 2: Simulate Private Search for 100 Random Numbers
# First digit should start from 6, 7, 8, or 9
random_numbers = []
for _ in range(1000):
    first_digit = random.choice(['6', '7', '8', '9'])
    remaining_digits = "".join(random.choices("0123456789", k=9))  # Generate next 9 digits
    random_number = first_digit + remaining_digits
    random_numbers.append(random_number)

print(f"Client is searching for the following 100 random numbers...\n")

# Step 3: Perform Search for Each Random Number
for client_number in random_numbers:
    prefix = ""
    found = True
    r = random.randint(1, 10)  # Random value for privacy

    print(f"\nSearching for number: {client_number}")
    for index, digit in enumerate(client_number):
        # Encrypt the current digit
        encrypted_digit = ts.bfv_vector(context, [int(digit)])

        # Server checks the lane corresponding to the current prefix
        server_lanes = trie.search_lane(prefix)
        if not server_lanes:
            print(f"Number {client_number} not found.")
            found = False
            break

        # Perform homomorphic digit match
        results = private_digit_match(server_lanes, encrypted_digit, r, context)

        # Client decrypts the results
        decrypted_results = [(res.decrypt()[0], lane, loc) for res, lane, loc in results]

        # Check if any result is 0 (indicating a match)
        matched = False
        for decrypted_value, lane, loc in decrypted_results:
            if decrypted_value == 0:
                matched = True
                prefix += digit
                print(f"Match found for digit {digit} at lane {lane}, location {loc}.")
                break

        if not matched:
            print(f"Number {client_number} not found at digit {index + 1}.")
            found = False
            break

    if found:
        print(f"Number {client_number} is present in the server.")

# End the timer
end_time = time.time()
execution_time = end_time - start_time

print(f"\nExecution Time for 1000 Random Numbers: {execution_time:.2f} seconds")


Client is searching for the following 100 random numbers...


Searching for number: 7109401871
Match found for digit 7 at lane 9, location 1.
Match found for digit 1 at lane 23, location 1.
Match found for digit 0 at lane 180, location 1.
Match found for digit 9 at lane 7873, location 1.
Number 7109401871 not found at digit 5.

Searching for number: 7597228593
Match found for digit 7 at lane 9, location 1.
Match found for digit 5 at lane 65, location 1.
Match found for digit 9 at lane 78, location 1.
Match found for digit 7 at lane 340, location 1.
Number 7597228593 not found at digit 5.

Searching for number: 7892219522
Match found for digit 7 at lane 9, location 1.
Match found for digit 8 at lane 9, location 2.
Match found for digit 9 at lane 9, location 3.
Match found for digit 2 at lane 9, location 4.
Number 7892219522 not found at digit 5.

Searching for number: 6782700568
Match found for digit 6 at lane 2, location 1.
Match found for digit 7 at lane 4, location 1.
Match found for

In [ ]:
import tenseal as ts
import time
from collections import defaultdict
import csv
import random


class TrieNode:
    """Node structure for hierarchical data storage."""
    def __init__(self):
        self.children = defaultdict(TrieNode)
        self.lane_locations = {}  # Maps digit to (lane, location)


class MobileNumberTrie:
    """Trie structure to store mobile numbers hierarchically."""
    def __init__(self):
        self.root = TrieNode()
        self.lane_counter = 1
        self.location_counter = 1

    def insert(self, number):
        """Insert a number into the trie and assign lane and location."""
        current = self.root
        for digit in number:
            if digit not in current.lane_locations:
                current.lane_locations[digit] = (self.lane_counter, self.location_counter)
                self.location_counter += 1
            current = current.children[digit]
        self.lane_counter += 1
        self.location_counter = 1  # Reset location counter for each lane

    def search_lane(self, prefix):
        """Get the lane and locations for the given prefix."""
        current = self.root
        for digit in prefix:
            if digit in current.children:
                current = current.children[digit]
            else:
                return None  # Prefix not found
        return current.lane_locations


def read_mobile_numbers_from_csv(filename):
    """Reads mobile numbers from a CSV file."""
    mobile_numbers = []
    with open(filename, 'r') as file:
        reader = csv.reader(file)
        next(reader)  # Skip header
        for row in reader:
            mobile_numbers.append(row[0])  # Assuming the first column has the numbers
    return mobile_numbers


def private_digit_match(server_lanes, encrypted_digit, r, context):
    """Perform homomorphic computation for digit matching."""
    results = []
    for digit, (lane, location) in server_lanes.items():
        enc_digit = ts.bfv_vector(context, [int(digit)])  # Encrypt server digit
        result = (encrypted_digit - enc_digit) * r
        results.append((result, lane, location))
    return results


# Client-Side Encryption Setup
context = ts.context(ts.SCHEME_TYPE.BFV, poly_modulus_degree=8192, plain_modulus=1032193)
context.generate_galois_keys()

# Start the timer
start_time = time.time()

# Step 1: Read and Build the Trie
csv_filename = "mobile_numbers.csv"
mobile_numbers = read_mobile_numbers_from_csv(csv_filename)

trie = MobileNumberTrie()
for number in mobile_numbers:
    trie.insert(number)

# Step 2: Simulate Private Search for 100 Random Numbers
# First digit should start from 6, 7, 8, or 9
random_numbers = []
for _ in range(10000):
    first_digit = random.choice(['6', '7', '8', '9'])
    remaining_digits = "".join(random.choices("0123456789", k=9))  # Generate next 9 digits
    random_number = first_digit + remaining_digits
    random_numbers.append(random_number)

print(f"Client is searching for the following 100 random numbers...\n")

# Step 3: Perform Search for Each Random Number
for client_number in random_numbers:
    prefix = ""
    found = True
    r = random.randint(1, 10)  # Random value for privacy

    print(f"\nSearching for number: {client_number}")
    for index, digit in enumerate(client_number):
        # Encrypt the current digit
        encrypted_digit = ts.bfv_vector(context, [int(digit)])

        # Server checks the lane corresponding to the current prefix
        server_lanes = trie.search_lane(prefix)
        if not server_lanes:
            print(f"Number {client_number} not found.")
            found = False
            break

        # Perform homomorphic digit match
        results = private_digit_match(server_lanes, encrypted_digit, r, context)

        # Client decrypts the results
        decrypted_results = [(res.decrypt()[0], lane, loc) for res, lane, loc in results]

        # Check if any result is 0 (indicating a match)
        matched = False
        for decrypted_value, lane, loc in decrypted_results:
            if decrypted_value == 0:
                matched = True
                prefix += digit
                print(f"Match found for digit {digit} at lane {lane}, location {loc}.")
                break

        if not matched:
            print(f"Number {client_number} not found at digit {index + 1}.")
            found = False
            break

    if found:
        print(f"Number {client_number} is present in the server.")

# End the timer
end_time = time.time()
execution_time = end_time - start_time

print(f"\nExecution Time for 10000 Random Numbers: {execution_time:.2f} seconds")


Client is searching for the following 100 random numbers...


Searching for number: 8934780051
Match found for digit 8 at lane 1, location 1.
Match found for digit 9 at lane 27, location 1.
Match found for digit 3 at lane 27, location 2.
Match found for digit 4 at lane 836, location 1.
Number 8934780051 not found at digit 5.

Searching for number: 6933757612
Match found for digit 6 at lane 2, location 1.
Match found for digit 9 at lane 47, location 1.
Match found for digit 3 at lane 467, location 1.
Match found for digit 3 at lane 1025, location 1.
Number 6933757612 not found at digit 5.

Searching for number: 7814631163
Match found for digit 7 at lane 9, location 1.
Match found for digit 8 at lane 9, location 2.
Match found for digit 1 at lane 215, location 1.
Match found for digit 4 at lane 14535, location 1.
Number 7814631163 not found at digit 5.

Searching for number: 7795556021
Match found for digit 7 at lane 9, location 1.
Match found for digit 7 at lane 48, location 1.
Match fo